<a href="https://colab.research.google.com/github/utkar22/CSE508_Winter2023_Group2_Project/blob/main/Censoring/VOSK.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip3 install vosk
!pip install pydub
!pip install pydub
!apt install ffmpeg

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 35.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.7/129.7 kB 6.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for srt: filename=srt-3.5.3-py3-none-any.whl size=22445 sha256=f4af17488ab61334a31823664c0473c4520b30ff2914ac5d7d1acf6cd65721e7
  Stored in directory: /root/.cache/pip/wheels/69/cb/6a/5e5977c5c1fab3b94ff429718103884855b0d5671ed9880100
Successfully built srt


In [88]:
import subprocess
import sys
import os

from vosk import Model, KaldiRecognizer, SetLogLevel
from pydub import AudioSegment

import wave
from scipy.io import wavfile

from pydub.silence import split_on_silence

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [89]:
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/MyDrive/IR_Project

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [91]:
def mp3_to_wav(source, skip=0, excerpt=False):
    
    sound = AudioSegment.from_mp3(source) # load source
    sound = sound.set_channels(1) # mono
    sound = sound.set_frame_rate(16000) # 16000Hz
    
    if excerpt:
        excrept = sound[skip*1000:skip*1000+30000] # 30 seconds - Does not work anymore when using skip
        output_path = os.path.splitext(source)[0]+"_excerpt.wav"
        excrept.export(output_path, format="wav")
    else:
        audio = sound[skip*1000:]
        output_path = os.path.splitext(source)[0]+".wav"
        audio.export(output_path, format="wav")
    
    return output_path

In [122]:
wf = wave.open("obama.wav", "rb")

SAMPLE_RATE = 16000

SetLogLevel(0)

model = Model(lang="en-us")
rec = KaldiRecognizer(model, wf.getframerate())
rec.SetWords(True)

import json

# To store our results
transcription = []

out_result=[]

while True:
    data = wf.readframes(4000)
    if len(data) == 0:
        break
    if rec.AcceptWaveform(data):
        # Convert json output to dict
        result_dict = json.loads(rec.Result())
        print(result_dict)
        try:
            out_result.extend(result_dict['result'])
        except:
            pass
        # Extract text values and append them to transcription list
        transcription.append(result_dict.get("text", ""))

print(out_result)
# Get final bits of audio and flush the pipeline
final_result = json.loads(rec.FinalResult())
# print(transcription)
transcription.append(final_result.get("text", ""))

# merge or join all list elements to one big string
transcription_text = ' '.join(transcription)
print(transcription_text)


{'result': [{'conf': 0.324643, 'end': 1.5, 'start': 1.29, 'word': 'no'}], 'text': 'no'}
{'result': [{'conf': 1.0, 'end': 6.57, 'start': 6.24, 'word': 'yeah'}], 'text': 'yeah'}
{'result': [{'conf': 0.48016, 'end': 7.35, 'start': 7.2, 'word': 'a'}, {'conf': 0.453414, 'end': 7.98, 'start': 7.394493, 'word': 'show'}], 'text': 'a show'}
{'result': [{'conf': 1.0, 'end': 9.528868, 'start': 8.88, 'word': 'the'}], 'text': 'the'}
{'result': [{'conf': 0.627697, 'end': 12.57, 'start': 12.15, 'word': 'ah'}], 'text': 'ah'}
{'result': [{'conf': 0.560736, 'end': 17.361174, 'start': 16.8, 'word': 'ty'}, {'conf': 0.497556, 'end': 17.88, 'start': 17.778918, 'word': 'a'}, {'conf': 1.0, 'end': 18.33, 'start': 17.94, 'word': 'lot'}, {'conf': 1.0, 'end': 18.42, 'start': 18.33, 'word': 'of'}, {'conf': 1.0, 'end': 18.96, 'start': 18.45, 'word': 'shit'}], 'text': 'ty a lot of shit'}
{'text': ''}
{'result': [{'conf': 0.924709, 'end': 28.08, 'start': 27.69, 'word': 'try'}, {'conf': 1.0, 'end': 28.62, 'start': 28.

In [123]:
word_start_end = {}

for i in out_result:
    word = i["word"]
    start = i["start"]
    end = i["end"]
    curr = [start,end]

    if word not in word_start_end:
        word_start_end[word] = []
    word_start_end[word].append(curr)

In [124]:
word_start_end

{'no': [[1.29, 1.5]],
 'yeah': [[6.24, 6.57], [36.42, 36.78], [141.63, 142.05]],
 'a': [[7.2, 7.35], [17.778918, 17.88], [91.08, 91.294197]],
 'show': [[7.394493, 7.98]],
 'the': [[8.88, 9.528868],
  [75.21, 75.48],
  [78.54, 79.23],
  [102.66, 103.2],
  [103.727285, 103.86],
  [137.67, 137.773345],
  [149.303862, 149.64],
  [162.72, 162.897026]],
 'ah': [[12.15, 12.57], [113.22, 113.73]],
 'ty': [[16.8, 17.361174]],
 'lot': [[17.94, 18.33]],
 'of': [[18.33, 18.42], [92.524036, 92.67]],
 'shit': [[18.45, 18.96], [113.76, 114.21]],
 'try': [[27.69, 28.08]],
 'that': [[28.44, 28.62],
  [49.44, 49.89],
  [122.19, 122.60469],
  [138.42, 138.78],
  [142.2, 142.71],
  [144.12, 144.42]],
 'at': [[28.62, 28.8]],
 'last': [[28.8, 29.49]],
 'and': [[38.25, 38.55]],
 'i': [[38.55, 38.64], [101.64, 101.85]],
 'half': [[39.18, 39.78]],
 'in': [[42.27, 42.39]],
 'word': [[42.75, 43.2]],
 'or': [[43.26, 43.574615], [79.53, 79.646404]],
 'cash': [[43.584192, 44.13]],
 'now': [[46.23, 46.89]],
 'wash':

In [113]:
word_to_be_bleeped = "and"

In [114]:
timestamps = word_start_end[word_to_be_bleeped]

In [115]:
timestamps

[[13.83, 13.98],
 [22.53, 22.77],
 [27.863416, 28.02],
 [40.23, 40.47],
 [54.12, 54.33],
 [70.47, 70.98],
 [77.85, 78.09],
 [84.75, 84.93],
 [87.84, 88.17],
 [100.98, 101.22],
 [102.66, 102.952961],
 [105.27, 105.39],
 [107.04, 107.22],
 [111.75, 112.02],
 [117.48, 117.66],
 [158.73, 158.878931],
 [218.85, 219.035273],
 [244.77, 245.050195],
 [253.74, 253.94918],
 [270.27, 270.63],
 [279.3, 279.414229]]

In [119]:
audio = AudioSegment.from_wav("monorail.wav")

In [120]:
bleep_volume = 30

for i in timestamps:
    end = i[1]
    start = i[0]

    print(f"Start time: {start}\nEnd Time: {end}")
    
    duration = (end - start)*1000
    print(f"Duration of the word segment: {duration}")
    
    # Create a bleep sound segment with the same duration as the word segment and apply gain
    bleep_sound = AudioSegment.silent(duration=duration).fade_in(50).fade_out(50)
    bleep_sound = bleep_sound.apply_gain(bleep_volume)
    print(f"Duration of the bleep segment: {len(bleep_sound)}")
    
    # Overlay the bleep sound over the word segment
    audio = audio.overlay(bleep_sound, position=start*1000, loop=False, gain_during_overlay=-30)


Start time: 13.83
End Time: 13.98
Duration of the word segment: 150.00000000000034
Duration of the bleep segment: 150
Start time: 22.53
End Time: 22.77
Duration of the word segment: 239.99999999999844
Duration of the bleep segment: 240
Start time: 27.863416
End Time: 28.02
Duration of the word segment: 156.58399999999872
Duration of the bleep segment: 157
Start time: 40.23
End Time: 40.47
Duration of the word segment: 240.000000000002
Duration of the bleep segment: 240
Start time: 54.12
End Time: 54.33
Duration of the word segment: 210.00000000000085
Duration of the bleep segment: 210
Start time: 70.47
End Time: 70.98
Duration of the word segment: 510.0000000000051
Duration of the bleep segment: 510
Start time: 77.85
End Time: 78.09
Duration of the word segment: 240.0000000000091
Duration of the bleep segment: 240
Start time: 84.75
End Time: 84.93
Duration of the word segment: 180.00000000000682
Duration of the bleep segment: 180
Start time: 87.84
End Time: 88.17
Duration of the word s

In [64]:
audio.export("output_audio.wav", format="wav")

<_io.BufferedRandom name='output_audio.wav'>

In [121]:
audio